**GOLD (Business Logic)**

In [0]:
from pyspark.sql.functions import col, when

gold_results = (
    spark.table("exam_analytics.silver_students")
    .join(
        spark.table("exam_analytics.category_cutoff"),
        on="category",
        how="left"
    )
    .withColumn(
        "pass_status",
        when(col("marks") >= col("cutoff_percentage"), "Pass")
        .otherwise("Fail")
    )
)

gold_results.write.mode("overwrite").saveAsTable("exam_analytics.gold_results")

display(gold_results.limit(10))


category student_id name city marks attendance_status attempt_number exam_date cutoff_percentage pass_status General 1 Rakesh_1 Delhi 0 Absent 1 2026-01-08 60 Fail General 2 Neha_2 Mumbai 76 Present 3 2026-01-09 60 Pass General 3 Ritu_3 Delhi 75 Present 1 2026-01-03 60 Pass OBC 4 Neha_4 Bhopal 85 Present 3 2026-02-02 55 Pass General 5 Vikas_5 Lucknow 0 Absent 1 2026-02-15 60 Fail General 6 Nitin_6 Hyderabad 65 Present 1 2026-02-07 60 Pass General 7 Kunal_7 Pune 0 Absent 1 2026-01-28 60 Fail General 8 Vikas_8 Pune 84 Present 1 2026-02-18 60 Pass OBC 9 Suresh_9 Pune 0 Absent 3 2026-01-07 55 Fail General 10 Arjun_10 Delhi 0 Absent 3 2026-02-21 60 Fail

In [0]:
from pyspark.sql.functions import count

pass_kpi = (
    spark.table("exam_analytics.gold_results")
    .groupBy("category", "pass_status")
    .agg(count("*").alias("student_count"))
)

pass_kpi.write.mode("overwrite").saveAsTable("exam_analytics.gold_pass_kpi")


**Merit Ranking (Top students)[](url)**

In [0]:
from pyspark.sql.window import Window
from pyspark.sql.functions import dense_rank, col

# Filter only present students
present_students = gold_results.filter(col("attendance_status") == "Present")

# Rank only present students (NO skipped ranks)
window_spec = Window.orderBy(col("marks").desc())

ranked_df = present_students.withColumn("rank", dense_rank().over(window_spec))

ranked_df.write.mode("overwrite").saveAsTable("exam_analytics.gold_rankings")

# Show all present students in merit order
display(ranked_df.orderBy(col("rank")))


/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


category student_id name city marks attendance_status attempt_number exam_date cutoff_percentage pass_status rank General 3850 Ritu_3850 Pune 95 Present 1 2026-01-25 60 Pass 1 EWS 985 Meera_985 Lucknow 95 Present 2 2026-01-22 50 Pass 1 General 977 Tarun_977 Bangalore 94 Present 1 2026-02-21 60 Pass 2 General 1321 Kiran_1321 Kolkata 94 Present 1 2026-02-20 60 Pass 2 General 1011 Komal_1011 Lucknow 93 Present 3 2026-03-01 60 Pass 3 General 5210 Ritu_5210 Bangalore 93 Present 2 2026-02-16 60 Pass 3 OBC 3936 Suresh_3936 Kolkata 93 Present 1 2026-01-18 55 Pass 3 EWS 12543 Rakesh_12543 Hyderabad 92 Present 1 2026-02-11 50 Pass 4 General 3844 Manish_3844 Hyderabad 92 Present 2 2026-01-10 60 Pass 4 EWS 2092 Pradeep_2092 Lucknow 92 Present 1 2026-02-26 50 Pass 4 General 1723 Isha_1723 Chennai 92 Present 1 2026-02-08 60 Pass 4 SC 15579 Neha_15579 Jaipur 92 Present 1 2026-01-16 null Fail 4 EWS 42456 Kavita_42456 Chennai 91 Present 2 2026-01-18 50 Pass 5 OBC 45247 Nitin_45247 Bhopal 91 Present 1 2026-01-07 55 Pass 5 SC 48335 Suresh_48335 Delhi 91 Present 1 2026-02-26 null Fail 5 General 2524 Sahil_2524 Bangalore 91 Present 1 2026-02-08 60 Pass 5 General 8210 Suresh_8210 Chennai 91 Present 2 2026-02-05 60 Pass 5 General 27722 Harsh_27722 Mumbai 91 Present 3 2026-01-08 60 Pass 5 General 5969 Kiran_5969 Delhi 91 Present 3 2026-01-08 60 Pass 5 General 26542 Neha_26542 Mumbai 91 Present 1 2026-01-18 60 Pass 5 General 8530 Kavita_8530 Chennai 91 Present 1 2026-01-23 60 Pass 5 EWS 5486 Pradeep_5486 Mumbai 91 Present 2 2026-03-01 50 Pass 5 General 48811 Pradeep_48811 Delhi 91 Present 1 2026-01-09 60 Pass 5 OBC 22414 Kiran_22414 Bhopal 91 Present 3 2026-02-09 55 Pass 5 EWS 15238 Rahul_15238 Bhopal 91 Present 1 2026-01-06 50 Pass 5 OBC 14176 Simran_14176 Bhopal 91 Present 3 2026-02-22 55 Pass 5 OBC 20623 Kunal_20623 Pune 91 Present 3 2026-01-08 55 Pass 5 OBC 9064 Komal_9064 Bangalore 91 Present 3 2026-02-05 55 Pass 5 EWS 44362 Anita_44362 Hyderabad 91 Present 1 2026-02-06 50 Pass 5 OBC 39299 Anita_39299 Jaipur 91 Present 3 2026-02-26 55 Pass 5 General 37182 Nitin_37182 Pune 91 Present 2 2026-01-19 60 Pass 5 General 30568 Nitin_30568 Jaipur 91 Present 1 2026-02-24 60 Pass 5 General 25266 Vikas_25266 Delhi 91 Present 2 2026-02-04 60 Pass 5 General 16030 Neha_16030 Hyderabad 91 Present 1 2026-01-01 60 Pass 5 General 31388 Neha_31388 Lucknow 91 Present 1 2026-01-17 60 Pass 5 OBC 33556 Priya_33556 Jaipur 91 Present 2 2026-02-20 55 Pass 5 EWS 29058 Kavita_29058 Lucknow 91 Present 3 2026-03-02 50 Pass 5 General 41699 Rakesh_41699 Delhi 91 Present 2 2026-02-23 60 Pass 5 OBC 29587 Priya_29587 Bangalore 91 Present 1 2026-02-19 55 Pass 5 SC 9089 Suresh_9089 Mumbai 91 Present 1 2026-01-31 null Fail 5 OBC 9882 Komal_9882 Chennai 91 Present 3 2026-01-25 55 Pass 5 General 33460 Divya_33460 Hyderabad 91 Present 1 2026-01-29 60 Pass 5 General 14039 Pooja_14039 Delhi 91 Present 3 2026-01-27 60 Pass 5 General 49578 Isha_49578 Lucknow 91 Present 3 2026-02-19 60 Pass 5 EWS 29886 Neha_29886 Chennai 91 Present 3 2026-02-22 50 Pass 5 OBC 20124 Rakesh_20124 Kolkata 91 Present 1 2026-02-22 55 Pass 5 OBC 17603 Sneha_17603 Lucknow 91 Present 1 2026-01-09 55 Pass 5 SC 14219 Suresh_14219 Mumbai 91 Present 3 2026-01-09 null Fail 5 General 35666 Divya_35666 Bhopal 91 Present 3 2026-01-14 60 Pass 5 SC 44368 Pooja_44368 Pune 91 Present 3 2026-01-16 null Fail 5 General 14175 Nitin_14175 Jaipur 91 Present 3 2026-02-05 60 Pass 5 General 14893 Kiran_14893 Jaipur 91 Present 2 2026-01-05 60 Pass 5 OBC 33436 Simran_33436 Bangalore 91 Present 3 2026-01-07 55 Pass 5 OBC 46758 Divya_46758 Bangalore 91 Present 3 2026-02-28 55 Pass 5 OBC 36635 Sneha_36635 Kolkata 91 Present 2 2026-02-12 55 Pass 5 SC 17775 Arjun_17775 Bhopal 91 Present 3 2026-01-01 null Fail 5 OBC 17544 Sneha_17544 Kolkata 91 Present 2 2026-01-30 55 Pass 5 OBC 16344 Tarun_16344 Jaipur 91 Present 2 2026-01-08 55 Pass 5 OBC 19989 Kiran_19989 Bangalore 91 Present 2 2026-02-24 55 Pass 5 General 12576 Tarun_12576 Lucknow 91 Present 

**Pass % by Category (KPI)**

In [0]:
from pyspark.sql.functions import col, avg

pass_stats = (
    gold_results
    .groupBy("category")
    .agg(
        (avg((col("pass_status") == "Pass").cast("int")) * 100)
        .alias("pass_percentage")
    )
)

display(pass_stats)


category pass_percentage OBC 45.09375207049626 SC 0.0 General 40.875033449290875 EWS 48.24100283057015

**Low Performers (At Risk Students)**

In [0]:
from pyspark.sql.functions import col

low_performers = (
    gold_results
    .filter(
        (col("attendance_status") == "Present") &
        (col("marks") < col("cutoff_percentage"))
    )
)

display(low_performers)
 

category student_id name city marks attendance_status attempt_number exam_date cutoff_percentage pass_status General 131 Amit_131 Kolkata 45 Present 3 2026-01-15 60 Fail EWS 461 Nitin_461 Delhi 44 Present 2 2026-01-05 50 Fail OBC 612 Rakesh_612 Bangalore 46 Present 2 2026-01-01 55 Fail OBC 675 Arjun_675 Mumbai 48 Present 3 2026-02-18 55 Fail General 729 Rohit_729 Mumbai 43 Present 2 2026-02-16 60 Fail General 849 Manish_849 Mumbai 53 Present 2 2026-01-17 60 Fail General 850 Sneha_850 Kolkata 56 Present 3 2026-02-26 60 Fail General 870 Ritu_870 Jaipur 57 Present 2 2026-02-04 60 Fail General 905 Vikas_905 Kolkata 48 Present 3 2026-01-18 60 Fail General 951 Simran_951 Bhopal 49 Present 1 2026-01-02 60 Fail General 963 Kunal_963 Hyderabad 47 Present 1 2026-01-27 60 Fail OBC 984 Meera_984 Lucknow 40 Present 3 2026-02-13 55 Fail OBC 1023 Suresh_1023 Delhi 46 Present 1 2026-01-10 55 Fail General 1036 Sneha_1036 Hyderabad 56 Present 2 2026-02-07 60 Fail General 1054 Vikas_1054 Kolkata 52 Present 3 2026-02-04 60 Fail General 1062 Meera_1062 Pune 48 Present 2 2026-01-05 60 Fail General 1068 Tarun_1068 Pune 55 Present 3 2026-02-28 60 Fail OBC 1069 Meera_1069 Bangalore 52 Present 1 2026-02-05 55 Fail General 1104 Arjun_1104 Lucknow 50 Present 2 2026-02-07 60 Fail General 1150 Rakesh_1150 Hyderabad 53 Present 1 2026-02-03 60 Fail General 1162 Sneha_1162 Lucknow 53 Present 3 2026-01-27 60 Fail General 1168 Rohit_1168 Chennai 37 Present 2 2026-01-25 60 Fail General 1199 Pooja_1199 Bangalore 57 Present 1 2026-02-14 60 Fail General 1236 Arjun_1236 Kolkata 51 Present 3 2026-01-06 60 Fail General 1239 Vikas_1239 Mumbai 52 Present 1 2026-02-24 60 Fail General 1260 Kavita_1260 Delhi 50 Present 3 2026-01-16 60 Fail General 1262 Deepak_1262 Chennai 38 Present 2 2026-01-06 60 Fail General 1264 Anita_1264 Pune 58 Present 3 2026-01-04 60 Fail OBC 1272 Isha_1272 Lucknow 49 Present 1 2026-02-25 55 Fail General 1308 Arjun_1308 Hyderabad 52 Present 3 2026-02-21 60 Fail General 1324 Ritu_1324 Bangalore 50 Present 2 2026-02-19 60 Fail OBC 1372 Simran_1372 Chennai 45 Present 1 2026-02-12 55 Fail General 1374 Manish_1374 Jaipur 48 Present 2 2026-02-25 60 Fail General 1389 Harsh_1389 Kolkata 57 Present 2 2026-02-15 60 Fail OBC 1390 Sunita_1390 Delhi 54 Present 2 2026-01-25 55 Fail General 1397 Tarun_1397 Chennai 59 Present 3 2026-02-01 60 Fail OBC 1404 Sneha_1404 Hyderabad 52 Present 2 2026-01-11 55 Fail OBC 1410 Vikas_1410 Delhi 41 Present 3 2026-02-09 55 Fail General 1414 Pradeep_1414 Pune 44 Present 3 2026-02-09 60 Fail General 1446 Deepak_1446 Hyderabad 45 Present 3 2026-02-12 60 Fail General 1481 Anjali_1481 Jaipur 55 Present 1 2026-02-06 60 Fail General 1493 Kiran_1493 Bangalore 56 Present 1 2026-02-25 60 Fail General 1505 Rohit_1505 Bhopal 52 Present 1 2026-02-03 60 Fail General 1523 Simran_1523 Pune 50 Present 3 2026-02-23 60 Fail General 1541 Pooja_1541 Bhopal 49 Present 2 2026-01-06 60 Fail General 1557 Suresh_1557 Mumbai 47 Present 1 2026-02-24 60 Fail OBC 1560 Kiran_1560 Delhi 41 Present 2 2026-01-26 55 Fail General 1588 Kunal_1588 Jaipur 59 Present 1 2026-02-21 60 Fail General 1632 Ritu_1632 Hyderabad 55 Present 3 2026-02-18 60 Fail General 1637 Kunal_1637 Chennai 57 Present 2 2026-02-19 60 Fail General 1639 Deepak_1639 Chennai 50 Present 2 2026-02-07 60 Fail General 1669 Kunal_1669 Jaipur 49 Present 1 2026-01-08 60 Fail General 1686 Sunita_1686 Bhopal 42 Present 1 2026-01-30 60 Fail General 1705 Priya_1705 Pune 56 Present 3 2026-02-14 60 Fail OBC 1708 Manish_1708 Bangalore 51 Present 1 2026-02-28 55 Fail General 1722 Kiran_1722 Delhi 49 Present 1 2026-02-12 60 Fail General 1783 Anjali_1783 Mumbai 48 Present 3 2026-02-17 60 Fail OBC 1796 Arjun_1796 Hyderabad 54 Present 2 2026-02-22 55 Fail EWS 1800 Sunita_1800 Kolkata 44 Present 1 2026-01-28 50 Fail General 1830 Nitin_1830 Bangalore 51 Present 2 2026-02-20 60 Fail OBC 1846 Anjali_1846 Hyderabad 49 Present 2 2026-01-14 55 Fail General 1871 Simran_1871 Hyderabad 45 Present 3 2026-02-02 60 Fail Genera

**Pass % by City**

In [0]:
from pyspark.sql.functions import col, avg, round, desc

pass_percentage_city = (
    gold_results
    .filter(col("attendance_status") == "Present")   # only present students (best practice)
    .groupBy("city")
    .agg(
        round(
            avg((col("pass_status") == "Pass").cast("int")) * 100,
            2
        ).alias("pass_percentage")
    )
    .orderBy(desc("pass_percentage"))
)

pass_percentage_city.write.mode("overwrite") \
    .saveAsTable("exam_analytics.gold_pass_percentage_city")

display(pass_percentage_city)


city pass_percentage Bhopal 74.79 Chennai 73.87 Mumbai 73.63 Lucknow 73.16 Bangalore 72.7 Pune 72.66 Hyderabad 72.59 Jaipur 72.35 Kolkata 72.17 Delhi 72.14

**Pass % by Category**

In [0]:
from pyspark.sql.functions import col, avg, round, desc

pass_percentage_category = (
    gold_results
    .filter(col("attendance_status") == "Present")
    .groupBy("category")
    .agg(
        round(
            avg((col("pass_status") == "Pass").cast("int")) * 100,
            2
        ).alias("pass_percentage")
    )
    .orderBy(desc("pass_percentage"))
)

pass_percentage_category.write.mode("overwrite") \
    .saveAsTable("exam_analytics.gold_pass_percentage_category")

display(pass_percentage_category)


category pass_percentage EWS 95.82 OBC 89.6 General 81.55 SC 0.0

**Attendance % by Category**

In [0]:
attendance_by_category = (
    gold_results
    .groupBy("category")
    .agg(
        round(
            avg((col("attendance_status") == "Present").cast("int")) * 100,
            2
        ).alias("attendance_percentage")
    )
)

attendance_by_category.write.mode("overwrite") \
    .saveAsTable("exam_analytics.gold_attendance_category")

display(attendance_by_category)


category attendance_percentage OBC 50.33 SC 50.66 General 50.12 EWS 50.34

**Avg Marks by Category**

In [0]:
avg_marks_category = (
    gold_results
    .filter(col("attendance_status") == "Present")
    .groupBy("category")
    .agg(round(avg("marks"),2).alias("avg_marks"))
)

avg_marks_category.write.mode("overwrite") \
    .saveAsTable("exam_analytics.gold_avg_marks_category")

display(avg_marks_category)


category avg_marks OBC 70.01 SC 69.77 General 70.1 EWS 70.41

**Attempt Trend**

In [0]:
attempt_trend = (
    gold_results
    .filter(col("attendance_status") == "Present")
    .groupBy("attempt_number")
    .agg(round(avg("marks"),2).alias("avg_marks"))
    .orderBy("attempt_number")
)

attempt_trend.write.mode("overwrite") \
    .saveAsTable("exam_analytics.gold_attempt_trend")

display(attempt_trend)

attempt_number avg_marks 1 70.04 2 69.83 3 70.29

**Low Performers (Present Only)**

In [0]:
low_performers = (
    gold_results
    .filter(
        (col("attendance_status") == "Present") &
        (col("marks") < col("cutoff_percentage"))
    )
)

low_performers.write.mode("overwrite") \
    .saveAsTable("exam_analytics.gold_low_performers")

display(low_performers)

category student_id name city marks attendance_status attempt_number exam_date cutoff_percentage pass_status General 131 Amit_131 Kolkata 45 Present 3 2026-01-15 60 Fail EWS 461 Nitin_461 Delhi 44 Present 2 2026-01-05 50 Fail OBC 612 Rakesh_612 Bangalore 46 Present 2 2026-01-01 55 Fail OBC 675 Arjun_675 Mumbai 48 Present 3 2026-02-18 55 Fail General 729 Rohit_729 Mumbai 43 Present 2 2026-02-16 60 Fail General 849 Manish_849 Mumbai 53 Present 2 2026-01-17 60 Fail General 850 Sneha_850 Kolkata 56 Present 3 2026-02-26 60 Fail General 870 Ritu_870 Jaipur 57 Present 2 2026-02-04 60 Fail General 905 Vikas_905 Kolkata 48 Present 3 2026-01-18 60 Fail General 951 Simran_951 Bhopal 49 Present 1 2026-01-02 60 Fail General 963 Kunal_963 Hyderabad 47 Present 1 2026-01-27 60 Fail OBC 984 Meera_984 Lucknow 40 Present 3 2026-02-13 55 Fail OBC 1023 Suresh_1023 Delhi 46 Present 1 2026-01-10 55 Fail General 1036 Sneha_1036 Hyderabad 56 Present 2 2026-02-07 60 Fail General 1054 Vikas_1054 Kolkata 52 Present 3 2026-02-04 60 Fail General 1062 Meera_1062 Pune 48 Present 2 2026-01-05 60 Fail General 1068 Tarun_1068 Pune 55 Present 3 2026-02-28 60 Fail OBC 1069 Meera_1069 Bangalore 52 Present 1 2026-02-05 55 Fail General 1104 Arjun_1104 Lucknow 50 Present 2 2026-02-07 60 Fail General 1150 Rakesh_1150 Hyderabad 53 Present 1 2026-02-03 60 Fail General 1162 Sneha_1162 Lucknow 53 Present 3 2026-01-27 60 Fail General 1168 Rohit_1168 Chennai 37 Present 2 2026-01-25 60 Fail General 1199 Pooja_1199 Bangalore 57 Present 1 2026-02-14 60 Fail General 1236 Arjun_1236 Kolkata 51 Present 3 2026-01-06 60 Fail General 1239 Vikas_1239 Mumbai 52 Present 1 2026-02-24 60 Fail General 1260 Kavita_1260 Delhi 50 Present 3 2026-01-16 60 Fail General 1262 Deepak_1262 Chennai 38 Present 2 2026-01-06 60 Fail General 1264 Anita_1264 Pune 58 Present 3 2026-01-04 60 Fail OBC 1272 Isha_1272 Lucknow 49 Present 1 2026-02-25 55 Fail General 1308 Arjun_1308 Hyderabad 52 Present 3 2026-02-21 60 Fail General 1324 Ritu_1324 Bangalore 50 Present 2 2026-02-19 60 Fail OBC 1372 Simran_1372 Chennai 45 Present 1 2026-02-12 55 Fail General 1374 Manish_1374 Jaipur 48 Present 2 2026-02-25 60 Fail General 1389 Harsh_1389 Kolkata 57 Present 2 2026-02-15 60 Fail OBC 1390 Sunita_1390 Delhi 54 Present 2 2026-01-25 55 Fail General 1397 Tarun_1397 Chennai 59 Present 3 2026-02-01 60 Fail OBC 1404 Sneha_1404 Hyderabad 52 Present 2 2026-01-11 55 Fail OBC 1410 Vikas_1410 Delhi 41 Present 3 2026-02-09 55 Fail General 1414 Pradeep_1414 Pune 44 Present 3 2026-02-09 60 Fail General 1446 Deepak_1446 Hyderabad 45 Present 3 2026-02-12 60 Fail General 1481 Anjali_1481 Jaipur 55 Present 1 2026-02-06 60 Fail General 1493 Kiran_1493 Bangalore 56 Present 1 2026-02-25 60 Fail General 1505 Rohit_1505 Bhopal 52 Present 1 2026-02-03 60 Fail General 1523 Simran_1523 Pune 50 Present 3 2026-02-23 60 Fail General 1541 Pooja_1541 Bhopal 49 Present 2 2026-01-06 60 Fail General 1557 Suresh_1557 Mumbai 47 Present 1 2026-02-24 60 Fail OBC 1560 Kiran_1560 Delhi 41 Present 2 2026-01-26 55 Fail General 1588 Kunal_1588 Jaipur 59 Present 1 2026-02-21 60 Fail General 1632 Ritu_1632 Hyderabad 55 Present 3 2026-02-18 60 Fail General 1637 Kunal_1637 Chennai 57 Present 2 2026-02-19 60 Fail General 1639 Deepak_1639 Chennai 50 Present 2 2026-02-07 60 Fail General 1669 Kunal_1669 Jaipur 49 Present 1 2026-01-08 60 Fail General 1686 Sunita_1686 Bhopal 42 Present 1 2026-01-30 60 Fail General 1705 Priya_1705 Pune 56 Present 3 2026-02-14 60 Fail OBC 1708 Manish_1708 Bangalore 51 Present 1 2026-02-28 55 Fail General 1722 Kiran_1722 Delhi 49 Present 1 2026-02-12 60 Fail General 1783 Anjali_1783 Mumbai 48 Present 3 2026-02-17 60 Fail OBC 1796 Arjun_1796 Hyderabad 54 Present 2 2026-02-22 55 Fail EWS 1800 Sunita_1800 Kolkata 44 Present 1 2026-01-28 50 Fail General 1830 Nitin_1830 Bangalore 51 Present 2 2026-02-20 60 Fail OBC 1846 Anjali_1846 Hyderabad 49 Present 2 2026-01-14 55 Fail General 1871 Simran_1871 Hyderabad 45 Present 3 2026-02-02 60 Fail Genera

**Top Students**

In [0]:
from pyspark.sql.window import Window
from pyspark.sql.functions import dense_rank

window_spec = Window.orderBy(col("marks").desc())

top_students = (
    gold_results
    .filter(col("attendance_status") == "Present")
    .withColumn("rank", dense_rank().over(window_spec))
    .filter(col("rank") <= 10)
)

top_students.write.mode("overwrite") \
    .saveAsTable("exam_analytics.gold_top_students")

display(top_students)


/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


category student_id name city marks attendance_status attempt_number exam_date cutoff_percentage pass_status rank EWS 985 Meera_985 Lucknow 95 Present 2 2026-01-22 50 Pass 1 General 3850 Ritu_3850 Pune 95 Present 1 2026-01-25 60 Pass 1 General 977 Tarun_977 Bangalore 94 Present 1 2026-02-21 60 Pass 2 General 1321 Kiran_1321 Kolkata 94 Present 1 2026-02-20 60 Pass 2 General 1011 Komal_1011 Lucknow 93 Present 3 2026-03-01 60 Pass 3 OBC 3936 Suresh_3936 Kolkata 93 Present 1 2026-01-18 55 Pass 3 General 5210 Ritu_5210 Bangalore 93 Present 2 2026-02-16 60 Pass 3 General 1723 Isha_1723 Chennai 92 Present 1 2026-02-08 60 Pass 4 EWS 2092 Pradeep_2092 Lucknow 92 Present 1 2026-02-26 50 Pass 4 General 3844 Manish_3844 Hyderabad 92 Present 2 2026-01-10 60 Pass 4 EWS 12543 Rakesh_12543 Hyderabad 92 Present 1 2026-02-11 50 Pass 4 SC 15579 Neha_15579 Jaipur 92 Present 1 2026-01-16 null Fail 4 General 1621 Tarun_1621 Kolkata 91 Present 1 2026-01-01 60 Pass 5 OBC 2218 Simran_2218 Chennai 91 Present 1 2026-01-28 55 Pass 5 General 2322 Simran_2322 Hyderabad 91 Present 3 2026-01-19 60 Pass 5 OBC 2505 Meera_2505 Bangalore 91 Present 2 2026-03-01 55 Pass 5 General 2524 Sahil_2524 Bangalore 91 Present 1 2026-02-08 60 Pass 5 OBC 3122 Rohit_3122 Chennai 91 Present 3 2026-02-16 55 Pass 5 OBC 3994 Anjali_3994 Hyderabad 91 Present 3 2026-02-01 55 Pass 5 OBC 4112 Ritu_4112 Delhi 91 Present 2 2026-02-25 55 Pass 5 General 4226 Pooja_4226 Kolkata 91 Present 3 2026-02-16 60 Pass 5 SC 4991 Kunal_4991 Mumbai 91 Present 2 2026-02-20 null Fail 5 General 5369 Pooja_5369 Bangalore 91 Present 3 2026-01-06 60 Pass 5 OBC 5436 Rohit_5436 Bangalore 91 Present 1 2026-02-11 55 Pass 5 EWS 5486 Pradeep_5486 Mumbai 91 Present 2 2026-03-01 50 Pass 5 General 5969 Kiran_5969 Delhi 91 Present 3 2026-01-08 60 Pass 5 SC 6114 Komal_6114 Mumbai 91 Present 3 2026-02-12 null Fail 5 OBC 6640 Ritu_6640 Delhi 91 Present 1 2026-01-13 55 Pass 5 General 6725 Rahul_6725 Delhi 91 Present 2 2026-02-02 60 Pass 5 General 7269 Harsh_7269 Kolkata 91 Present 3 2026-02-08 60 Pass 5 OBC 7989 Tarun_7989 Bangalore 91 Present 2 2026-02-05 55 Pass 5 General 8005 Kavita_8005 Kolkata 91 Present 3 2026-01-10 60 Pass 5 General 8210 Suresh_8210 Chennai 91 Present 2 2026-02-05 60 Pass 5 General 8530 Kavita_8530 Chennai 91 Present 1 2026-01-23 60 Pass 5 OBC 8719 Harsh_8719 Chennai 91 Present 2 2026-01-13 55 Pass 5 General 8804 Priya_8804 Jaipur 91 Present 1 2026-02-24 60 Pass 5 OBC 9064 Komal_9064 Bangalore 91 Present 3 2026-02-05 55 Pass 5 SC 9089 Suresh_9089 Mumbai 91 Present 1 2026-01-31 null Fail 5 EWS 9196 Manish_9196 Hyderabad 91 Present 2 2026-01-18 50 Pass 5 SC 9340 Kiran_9340 Kolkata 91 Present 2 2026-02-13 null Fail 5 SC 9354 Amit_9354 Hyderabad 91 Present 3 2026-01-28 null Fail 5 EWS 9713 Komal_9713 Bhopal 91 Present 3 2026-02-26 50 Pass 5 EWS 9881 Komal_9881 Kolkata 91 Present 1 2026-01-19 50 Pass 5 OBC 9882 Komal_9882 Chennai 91 Present 3 2026-01-25 55 Pass 5 General 10182 Sneha_10182 Mumbai 91 Present 3 2026-02-05 60 Pass 5 General 10520 Rohit_10520 Jaipur 91 Present 3 2026-01-02 60 Pass 5 OBC 10889 Nitin_10889 Hyderabad 91 Present 1 2026-01-17 55 Pass 5 General 11253 Isha_11253 Hyderabad 91 Present 2 2026-01-06 60 Pass 5 OBC 11281 Pradeep_11281 Pune 91 Present 3 2026-02-26 55 Pass 5 General 11318 Sneha_11318 Mumbai 91 Present 1 2026-01-05 60 Pass 5 SC 11337 Ritu_11337 Pune 91 Present 2 2026-02-21 null Fail 5 General 11646 Kunal_11646 Mumbai 91 Present 3 2026-02-25 60 Pass 5 EWS 11869 Nitin_11869 Bhopal 91 Present 1 2026-02-22 50 Pass 5 General 12397 Sneha_12397 Lucknow 91 Present 3 2026-01-04 60 Pass 5 General 12441 Neha_12441 Bangalore 91 Present 3 2026-02-10 60 Pass 5 General 12576 Tarun_12576 Lucknow 91 Present 1 2026-01-21 60 Pass 5 General 12734 Amit_12734 Pune 91 Present 1 2026-02-14 60 Pass 5 OBC 13303 Amit_13303 Hyderabad 91 Present 3 2026-01-23 55 Pass 5 General 13478 Pooja_13478 Mumbai 91 Present 2 2026-02-19 60 Pass 5 General 13520 Rahul_13520 Lucknow 91 Present 3 2026-01-07 60 Pass 5